# Geodesic on a Torus

We would like to find a *geodesic*, i.e., a shortest curve, on the surface of a regular torus.

The parametric equations of a regular torus centered at $(0,0,0)$ in spherical coordinates are

\begin{align*}
      x & = (c + a \cos \phi) \cos \theta, \\
      y & = (c + a \cos \phi) \sin \theta, \\
      z & = a \sin \theta,
\end{align*}

with $0 \leq \phi$, $\theta \leq 2 \pi$ and $0 < a < c$.

We represent our geodesic as a parametric curve $(x(t), y(t), z(t))$. In order for the curve to lie on the surface of the torus, it must satisfy the parametric equations above, and we can instead seek $(\phi(t), \theta(t))$ where, without loss of generality, $t \in [0, \, 1]$.

In [1]:
using Pkg
Pkg.activate("geodesic")
# Pkg.add(name="JuMP")
# Pkg.add("Ipopt")
# Pkg.add("Plots")
# Pkg.add("PlotlyJS")  # un backend pour Plots.jl basé sur Javascript

  Activating project at `~/cvs/MTH8408/notebooks_cours/geodesic`


In [2]:
using JuMP, Ipopt, Printf

[ Info: Precompiling JuMP [4076af6c-e467-56ae-b986-b466b2749572]
[ Info: Precompiling Ipopt [b6b21f68-93f8-5de0-b562-5493be1d77c9]


We begin by defining the parameters of our torus and the number of discretization points to approximate our geodesic:

In [3]:
const N = 100    # number of discretization points
const h = 1 / N  # discretization step size
const a = 1      # inner radius
const c = 3      # outer radius

3

We can now state boundary conditions defining the start and end points of the geodesic.

In [4]:
ϕstart = 0
ϕend = π
θstart = 0
θend = π

π = 3.1415926535897...

We declare our model and the solver we will use to solve it:

In [5]:
m = Model(Ipopt.Optimizer)

A JuMP Model
Feasibility problem with:
Variables: 0
Model mode: AUTOMATIC
CachingOptimizer state: EMPTY_OPTIMIZER
Solver name: Ipopt

It is possible to show that an element of length on the surface of the torus is given by

$$
\mathrm{d}\ell = \sqrt{a^2 \dot{\phi}(t)^2 + (c + a \cos(\phi(t)))^2 \dot{\theta}(t)^2} \ \mathrm{d}t.
$$

We discretize the objective $\int_0^1 \mathrm{d}\ell$ using the trapeze rule.

We are going to define variables to represent $\phi$, $\theta$ but also $\dot{\phi}$ and $\dot{\theta}$.

We  now associate variables with our model and specify initial values. The initial approximation samples the intervals uniformly.

In [6]:
@variable(m, 0 ≤ ϕ[k = 1:N] ≤ 2π, start = (k * (ϕend - ϕstart) / N));
@variable(m, 0 ≤ θ[k = 1:N] ≤ 2π, start = (k * (θend - θstart) / N));
@variable(m, dϕ[1:N], start = (ϕend - ϕstart) / N);
@variable(m, dθ[1:N], start = (θend - θstart) / N);

# another way of setting the initial guess
# dϕ0 = ones(N) * (ϕend - ϕstart) / N
# dθ0 = ones(N) * (θend - θstart) / N
# ϕ0 = zeros(N)
# θ0 = zeros(N)
# ϕ0[1] = ϕstart
# θ0[1] = θstart
# for k = 1 : N-1
#    ϕ0[k+1] = ϕ0[k] - h/2 * (dϕ0[k] + dϕ0[k+1])
#    θ0[k+1] = θ0[k] - h/2 * (θ0[k] + θ0[k+1])
# end
# setvalue(ϕ, ϕ0)
# setvalue(θ, θ0)
# setvalue(dϕ, dϕ0)
# setvalue(dθ, dθ0)

The expression of our discretized objective function will be quite long.
In order to write it more concisely, JuMP allows us to define a nonlinear expression that we will use in the definition of the objective:

In [7]:
@NLexpression(m, f[k = 1:N], a^2 * dϕ[k]^2 + (c + a * cos(ϕ[k]))^2 * dθ[k]^2);

The expression of the objective in terms of `f` is now quite simple:

In [8]:
@NLobjective(m, Min, h/2 * sum(sqrt(f[k]) + sqrt(f[k+1]) for k = 1 : N-1));  # trapeze composée

We are ready to state our constraints, which include the boundary conditions and the definitions of $\dot{\phi}$ and $\dot{\theta}$:

In [9]:
@constraint(m, ϕ[1] == ϕstart)
@constraint(m, ϕ[N] == ϕend)
@constraint(m, θ[1] == θstart)
@constraint(m, θ[N] == θend)
@constraint(m, derϕ[k = 1:N-1], ϕ[k+1] - ϕ[k] == h/2 * (dϕ[k] + dϕ[k+1]))
@constraint(m, derθ[k = 1:N-1], θ[k+1] - θ[k] == h/2 * (dθ[k] + dθ[k+1]));

Our model statement is complete. We now call the solver:

In [10]:
optimize!(m)


******************************************************************************
This program contains Ipopt, a library for large-scale nonlinear optimization.
 Ipopt is released as open source code under the Eclipse Public License (EPL).
         For more information visit https://github.com/coin-or/Ipopt
******************************************************************************

This is Ipopt version 3.14.4, running with linear solver MUMPS 5.4.1.

Number of nonzeros in equality constraint Jacobian...:      796
Number of nonzeros in inequality constraint Jacobian.:        0
Number of nonzeros in Lagrangian Hessian.............:      600

Total number of variables............................:      400
                     variables with only lower bounds:        0
                variables with lower and upper bounds:      200
                     variables with only upper bounds:        0
Total number of equality constraints.................:      202
Total number of inequality co

When the solver has finished, we retrieve the final objective value and the variables $(\phi(t), \theta(t))$:

In [11]:
L = objective_value(m)
ϕs = value.(ϕ)
θs = value.(θ)
L

8.628607264435189

In order to plot our geodesic on the surface of the torus, we must convert $(\phi(t), \theta(t))$ to $(x(t), y(t), z(t))$:

In [12]:
# convert our solution curve to (x,y,z) coordinates
xs = (c .+ a * cos.(ϕs)) .* cos.(θs)
ys = (c .+ a * cos.(ϕs)) .* sin.(θs)
zs = a * sin.(ϕs);

We are ready to plot a torus and superimpose our geodesic:

In [13]:
using Plots
plotlyjs()
linspace(from, to, npoints) = range(from, stop=to, length=npoints)

# plot a torus
M = 200
αs = linspace(0, 2π, M)
βs = linspace(0, 2π, M)
Xs = (c .+ a * cos.(αs)) * cos.(βs)'
Ys = (c .+ a * cos.(αs)) * sin.(βs)'
Zs = (a * sin.(αs)) * ones(M)'
plot3d(Xs, Ys, Zs, st=:surface, grid=false, c=:grays, axis=false, colorbar=false)

# add our curve
plot3d!(xs, ys, zs, linewidth=4, color=:red, title=@sprintf("Geodesic on a Torus (length=%.4f)", L), legend=false)

[ Info: Precompiling Plots [91a5bcdd-55d7-5caf-9e0b-520d859cae80]


WebIO._IJuliaInit()

Voir http://www.rdrop.com/~half/math/torus/torus.geodesics.pdf pour les solutions analytiques.